In [7]:
# file name with directory
import os
import glob

files = list(glob.glob(os.path.join("Test_VelocityField",'*.*')))
files.sort(key=os.path.getctime) 
files

['Test_VelocityField\\DoubleGyre2D0.txt',
 'Test_VelocityField\\DoubleGyre2D1.txt',
 'Test_VelocityField\\DoubleGyre2D2.txt',
 'Test_VelocityField\\DoubleGyre2D3.txt',
 'Test_VelocityField\\DoubleGyre2D4.txt']

## Quiver

In [8]:
# Ensure interactive plotting in Jupyter
%matplotlib inline 

import numpy as np
import matplotlib.pyplot as plt
from matplotlib.animation import FuncAnimation
from IPython.display import HTML

# List of files for animation (replace with your actual file paths)
file_data = files

# Function to load velocity data from a file
def load_velocity_data(filename):
    with open(filename, 'r') as file:
        filedData = file.readlines()

    # Parse dimensions
    cols = int(filedData[0].strip()) #width
    rows = int(filedData[1].strip()) #height
    depth = int(filedData[2].strip())  # Depth is 1 for 2D data
    time = float(filedData[3].strip())

    # Parse velocity components
    velocityData = np.array(
        [list(map(float, line.split())) for line in filedData[4:]], dtype=np.float32
    )

    # Reshape velocity data into grids
    # I start with the rows here because, in the C++ code, I read the data row by row
    # Reshape is a math function not a graphics function, so the ordering here is following the matrix order
    # [0,0   0,1   0,2]
    u = velocityData[:, 0].reshape(rows, cols)  # X-component
    v = velocityData[:, 1].reshape(rows, cols)  # Y-component

    # Create a meshgrid for plotting
    # Mesh grid is a ploting function, so the cols are the x and the rows are the y
    # [0,0   1,0   2,0]
    x, y = np.meshgrid(np.arange(cols), np.arange(rows), indexing = 'xy')

    return x, y, u, v, time

# Initialize the plot
fig, ax = plt.subplots(figsize=(10, 10))
x, y, u, v, time = load_velocity_data(file_data[0])  # Load the first frame
quiver = ax.quiver(x, y, u, v)  # Initial quiver plot
ax.set_title(f"Velocity Field at t = {time}")
ax.set_xlabel("X-axis")
ax.set_ylabel("Y-axis")

# Define the update function for animation
def update(frame):
    x, y, u, v, time = load_velocity_data(file_data[frame % len(file_data)])
    quiver.set_UVC(u, v)  # Update the quiver plot with new data
    ax.set_title(f"Velocity Field at t = {time}")

# Create the animation
anim = FuncAnimation(fig, update, frames=len(file_data), interval=1000, repeat=True)

# Close the current plot to prevent duplicate display
plt.close(fig)  # Close the figure to avoid duplicate output

# Display the animation in Jupyter using HTML
HTML(anim.to_jshtml())


## Heatmap Style and Streamlines

In [9]:
import numpy as np
import matplotlib.pyplot as plt
from matplotlib.animation import FuncAnimation
from IPython.display import HTML

file_data = files

# Function to load velocity data from a file
def load_velocity_data(filename):
    with open(filename, 'r') as file:
        filedData = file.readlines()

    # Parse dimensions
    cols = int(filedData[0].strip()) #width
    rows = int(filedData[1].strip()) #height
    depth = int(filedData[2].strip())  # Depth is 1 for 2D data
    time = float(filedData[3].strip())

    # Parse velocity components
    velocityData = np.array(
        [list(map(float, line.split())) for line in filedData[4:]], dtype=np.float32
    )

    # Reshape velocity data into grids
    u = velocityData[:, 0].reshape(rows, cols)  # X-component of velocity
    v = velocityData[:, 1].reshape(rows, cols)  # Y-component of velocity

    # Create meshgrid for plotting
    x, y = np.meshgrid(np.arange(cols), np.arange(rows))

    # Compute velocity magnitude for the heatmap
    magnitude = np.sqrt(u**2 + v**2)

    return x, y, u, v, magnitude, time, cols, rows, depth

# Initialize the plot
fig, ax = plt.subplots(figsize=(10, 10))

# Load the first frame to initialize the heatmap and streamlines
x, y, u, v, magnitude, time, width, height, depth = load_velocity_data(file_data[0])

# Plot the initial heatmap
heatmap = ax.imshow(
    magnitude, origin='lower', extent=[0, x.shape[1] - 1, 0, y.shape[0] - 1],
    cmap='plasma', alpha=0.6
)
fig.colorbar(heatmap, ax=ax, label='Velocity Magnitude')

# Initialize the streamplot and store it as a list
stream = [ax.streamplot(x, y, u, v, color='black', linewidth=1, density=1.5)]

# Set title and labels
ax.set_title(f"Velocity Field at t = {time}")
ax.set_xlabel("X-axis")
ax.set_ylabel("Y-axis")

# Update function for animation
def update(frame):

    # Load new data for the current frame
    x, y, u, v, magnitude, time, cols, rows, depth = load_velocity_data(file_data[frame % len(file_data)])
    
    # Erase everything
    ax.cla()

    # Set the axis limits to prevent empty regions
    ax.set_xlim(0, cols - 1)  # Limit X-axis to 0 to width-1
    ax.set_ylim(0, rows - 1)  # Limit Y-axis to 0 to height-1

    # Reinitialize the Heatmap
    heatmap = ax.imshow(
    magnitude, origin='lower', extent=[0, x.shape[1] - 1, 0, y.shape[0] - 1],
    cmap='plasma', alpha=0.6)

    # Update the heatmap with the new magnitude values
    heatmap.set_data(magnitude)
    
    # Remove old streamlines by accessing the first streamplot in the list
    #stream[0].lines.remove()  # Ensure the old streamlines are removed

    # Plot new streamlines and store them in the stream list
    stream[0] = ax.streamplot(x, y, u, v, color='black', linewidth=1, density=1.5)

    # Update the title to reflect the current time step
    ax.set_title(f"Velocity Field at t = {time}")
    
# Create the animation
anim = FuncAnimation(fig, update, frames=len(file_data), interval=1000, repeat=True)

# Close the current plot to prevent duplicate display
plt.close(fig)  # Close the figure to avoid duplicate output

# Display the animation in Jupyter
HTML(anim.to_jshtml())
